# Ancillary Pull Example

## Imports

In [1]:
import time
import os
import pandas as pd
from tyba_client.client import Client, Market, AncillaryService

PAT = os.environ["TYBA_PAT"]
client = Client(PAT)
# client = Client('Your PAT') #Insert your PAT here

# Relevant Data Classes
services = client.services
lmp = services.lmp
ancillary = services.ancillary

## Pricing Regions

In [2]:
as_regions = ancillary.get_pricing_regions(
    iso="CAISO",
    service=AncillaryService.REGULATION_UP,
    market=Market.DA).json()
as_regions = pd.DataFrame(as_regions)
as_regions

region  start_year  end_year
0    Pacific Northwest - SP15        2010      2025
1                        WAPA        2010      2025
2                        WAPA        2010      2025
3                        WAPA        2010      2025
4                        ZP26        2010      2025
..                        ...         ...       ...
219                      ZP26        2010      2025
220                    Mexico        2010      2025
221                      SMUD        2010      2025
222                    Sutter        2010      2025
223                      NP15        2010      2025

[224 rows x 3 columns]

## Helper Functions

In [3]:
def as_pull(services, regions, start_year, end_year):
    all_prices = {}
    for region in regions:
        for name, service in services.items():
            print(region,name)
            as_prices = ancillary.get_prices(
                iso="CAISO",
                service=service, 
                market=Market.DA,
                region=region,
                start_year=start_year,
                end_year=end_year,
            ).json()
            tdom = pd.to_datetime(as_prices['datetimes']).tz_localize(None)
            all_prices[(region,name)] = pd.DataFrame(as_prices['prices'],index=tdom,columns=[name])
    return pd.concat(all_prices,axis=1).droplevel(1,axis=1)

## Pull All Services & Single Region

In [4]:
services = {
    'reg_up':AncillaryService.REGULATION_UP,
    'reg_down':AncillaryService.REGULATION_DOWN,
    'reserves':AncillaryService.RESERVES,
}
regions = [
    'SP15',
]

In [5]:
as_prices = as_pull(services,regions,2019,2023)
as_prices = as_prices.droplevel(0,axis=1)

SP15 reg_up
SP15 reg_down
SP15 reserves


In [6]:
as_prices.head()

reg_up  reg_down  reserves
2019-01-01 00:00:00    8.17     15.29      1.00
2019-01-01 01:00:00    1.66      1.01      1.00
2019-01-01 02:00:00    1.59      1.01      0.25
2019-01-01 03:00:00    1.29      1.01      0.25
2019-01-01 04:00:00    7.42      1.39      0.25

In [24]:
as_prices.to_csv('example_sp15_ancillary_prices.csv')

## Pull All Services & Multiple Regions

In [7]:
services = {
    'reg_up':AncillaryService.REGULATION_UP,
    'reg_down':AncillaryService.REGULATION_DOWN,
    'reserves':AncillaryService.RESERVES,
}
regions = ['SP15','NP15']

In [8]:
as_prices2 = as_pull(services,regions,2021,2021)
as_prices2

SP15 reg_up
SP15 reg_down
SP15 reserves
NP15 reg_up
NP15 reg_down
NP15 reserves


SP15                     NP15                  
                    reg_up reg_down reserves reg_up reg_down reserves
2021-01-01 00:00:00   1.63    11.88     1.63   4.23     3.00     1.25
2021-01-01 01:00:00   1.63    13.93     1.63   4.23     2.70     1.25
2021-01-01 02:00:00   1.63    10.58     1.63   1.65     3.50     1.25
2021-01-01 03:00:00   1.63    10.66     1.63   1.65     3.90     1.25
2021-01-01 04:00:00   1.63    10.15     1.63   1.66     3.30     1.25
...                    ...      ...      ...    ...      ...      ...
2021-12-31 19:00:00   6.57     5.00     6.57   4.97     0.99     6.57
2021-12-31 20:00:00   6.46     5.13     6.46   6.46     4.87     6.46
2021-12-31 21:00:00   4.75     0.21     3.00   4.75     2.26     3.00
2021-12-31 22:00:00   5.15     4.00     5.00   0.40     1.99     5.00
2021-12-31 23:00:00   7.85     5.00     4.42   7.85     5.00     4.42

[8760 rows x 6 columns]